# Réseaux de neurones et classification d'images avec MLP

Le but de ce TP est de e familiariser avec la classification d'images sur un corpus d'images simples, avant d'approfondir la semaine prochaines sur des images plus réalistes.

Le but du TP est de remplir les zones de code vides pour implémenter un programme qui peut classer correctement les images (avec un taux d'erreur inférieur à 10% )

In [2]:
import torch
from torch.utils.data import Dataset, DataLoader


from torchvision import datasets
from torchvision.transforms import ToTensor, Compose, Resize
import matplotlib.pyplot as plt


## Utilisation GPU
le code suivant vérifie que le GPU est disponible, et l'utilise si c'est le cas.
Si la valeur de `use_cuda` est `False`, vous devez changer le type de machine pour avoir accès à un GPU.

In [3]:
use_cuda = torch.cuda.is_available()
print(use_cuda)
device = torch.device("cuda:0" if use_cuda else "cpu")

False


## Préparation des données

Torchvision contient des jeux de données pour entraîner et évaluer les réseaux.
Nous utilisons [MNIST](https://en.wikipedia.org/wiki/MNIST_database).

On récupère les données d'entraînement et de test, puis on réserve une partie des données d'entraînement, qu'on appelle données de validation, pour sélectionner le meilleur modèle.
Ensuite, on nomme les différentes classes d'images.

In [ ]:
training_data = datasets.MNIST(
    root="data",
    train=True,
    download=True,
    transform=ToTensor()
)

test_data = datasets.MNIST(
    root="data",
    train=False,
    download=True,
    transform=ToTensor()
)

training_data, val_data = torch.utils.data.random_split(training_data, [50000, 10000])

NB_CLASSES=10

labels_map = {
    0: "Zero",
    1: "One",
    2: "Two",
    3: "Three",
    4: "Four",
    5: "Five",
    6: "Six",
    7: "Seven",
    8: "Eight",
    9: "Nine",
}


Ce corpus est constitué d'images en noir et blanc de taille 28×28. Ces images représentent des chiffres réparties en 10 classes différentes.

Chacune des cases (28$\times$ 28=784) contient une valeur entre 0 et 1, qui indique un niveau de gris, avec 0 pour les points noirs et 1 pour les points blancs.

Notez bien que même si ces images peuvent être représentées par une matrice 28×28, elles sont en faites stockées comme des tenseurs 1×28×28 de façon à expliciter qu'au lieu des habituels 3 canaux RGB indiquant les couleurs, qu'on verra en détails la semaine prochaine, on n'a ici qu'un seul canal qui indique le niveau de gris.

La fonction suivante affiche une sélection aléatoire de chiffres:



In [ ]:
def display_examples(cols=5, rows=2, net=None, data=training_data):
  figure = plt.figure(figsize=(16, 8))
  for i in range(1, cols * rows + 1):
    sample_idx = torch.randint(len(data), size=(1,)).item()
    img, label = data[sample_idx]
    figure.add_subplot(rows, cols, i)

    if net is None:
      label = "Correct Label: " + labels_map[label]
    else:
      imgdev = img.to(device)
      scores = net(imgdev)
      pred = torch.argmax(scores)
      label = "Predicted Label: " + labels_map[pred.item()]

    plt.title(label)
    plt.axis("off")
    plt.imshow(img.squeeze(), cmap="gray")
  plt.show()

display_examples()

## On charge les données

pour pouvoir être chargées facilement on crée des `DataLoader` qui vont nous permettre d'itérer facilement sur les données



In [7]:
BATCH_SIZE=512 #nombre d'images à traiter en parallèle

train_dataloader = DataLoader(training_data, batch_size=BATCH_SIZE, shuffle=True, pin_memory=True)
val_dataloader = DataLoader(val_data, batch_size=BATCH_SIZE, shuffle=False, pin_memory=True)
test_dataloader = DataLoader(test_data, batch_size=BATCH_SIZE, shuffle=False, pin_memory=True)

On dispose maintenant d'itérateurs sur les données `next`. On peut écrire par exemple :



In [ ]:
# Display image and label.
train_iter = iter(train_dataloader) #get an iterator over data
train_features, train_labels = next(train_iter) # get a batch of data
print(f"Feature batch shape: {train_features.size()}")
print(f"Labels batch shape: {train_labels.size()}")
img = train_features[0].squeeze() # reformat the first pic as 28x28
label = train_labels[0]
plt.imshow(img, cmap="gray") #it's B&W
plt.show()
print(f"Label: {label}")

Que contient notre image ?

In [ ]:
print(img)

## Évaluation
La fonction suivante compare, pour un jeu de données passé en paramètre, la classe `argmax` calculée par un réseau et le label qui devait être prédit.
Si ces valeurs sont égales alors elles comptent pour de bonnes réponses.
On retourne le ratio de bonnes réponses.

In [11]:
def eval(net, dataloader, device):

  total_test = 0.0
  correct_test = 0.0

  net.eval()

  #iterate over data
  for local_batch, local_labels in dataloader:
    # Transfer to GPU
    local_batch, local_labels = local_batch.to(device), local_labels.to(device)

    preds = net(local_batch)
    total_test += preds.size(0)
    correct_test += (torch.argmax(preds, dim=1) == local_labels).sum()

  return correct_test/total_test

# Implémentation d'un Perceptron multicouche

Implementer la class MLP pour les perceptrons multicouches.

Le constructeur prend en entrée:

    input_size la taille du vecteur d'entrée
    hidden_sizes la liste des tailles des couches internes
    output_size la taille de la couche de sortie
    activation la classe qui implémente la fonction à appliquer après chaque transformation linéaire

Aide: vous pouvez utiliser la classe Sequential pour modéliser la liste des transformations de votre MLP

La fonction forward prend entrée une image. Il faut d'abord transformer l'image (le tenseur à 3 dimensions) en un vecteur, puis on applique successivement chaque transformation linéaire, suivie d'une activation si on n'est pas sur la dernière couche.

In [ ]:
class MLP(torch.nn.Module):

  def __init__(self, input_size, hidden_sizes, output_size, activation):
    super().__init__()

    #your code begins here
    pass
    #your code ends here

  def forward(self,x):
    #your code begins here
    pass
    #your code ends here


## Boucle d'entraînement

Écrire la fonction `train` qui implément la boucle d'apprentissage

In [ ]:
def train(net, optimizer, epochs, train_data, val_data, test_data, batch_size, device, eval_frq=10):

  loss_fn = torch.nn.CrossEntropyLoss()

  total_loss = 0.0

  n_batches = 0
  for epoch in range(epochs):

    net.train()
    # iterate through train data
    #   -> get new batch
    #   -> send it to device
    #   -> compute class scores with net
    #   -> compute loss and compute the gradient of the loss
    #   -> call step() on optimizer to perform SGD, reset gradients to zero

    #your code begins here
    pass
    #your code ends here

    # eval if it's time...
    if epoch % eval_frq == 0:
      print(f"Epoch: {epoch}, Mean loss: {total_loss/n_batches}")
      rv=eval(net, val_loader, device)
      #  --> Display eval scores rt and rv
      display_examples(cols=5, rows=2, net=net, data=val_data):
      rt=eval(net, test_loader, device)
      display_examples(cols=5, rows=2, net=net, data=test_data):



## Création du réseau

Donner les bon paramètres pour la création de `net`.


Enuiste, modifier la fonction `display_examples` pour que si le paramètre `net` n'est pas `None` alors au lieu d'afficher le label correct des images, on affiche le label prédit par `net`, c'est-à-dire la classes `argmax`.

In [ ]:
net = MLP(None, None, None, None)
net = net.to(device)

display_examples(net=net)

## TEST

In [ ]:

opt = torch.optim.SGD(net.parameters(),lr=0.1)

train(net, opt, epochs=50, train_data=training_data, val_data=val_data, test_data=test_data, batch_size=BATCH_SIZE, model_name="model", device=device, eval_frq=5)



## Autres choses

1. Changer la fonction d'activation (`tanh`, `sigmoid`, `ReLU` etc) et comparer la convergence.
1. Changer le `learning rate` ($\alpha$) de SGD, et comparer la vitesse de convergence
2. Au lieu de SGD, utiliser Adam et comparer les vitesses de convergence

